In [86]:
import pandas as pd
#pd.set_option('display.max_colwidth', None)
import googlemaps
import requests
import time
import json
import geopandas as gpd
from shapely.geometry import Point
import folium
from folium import plugins
import config

api_key = config.api_key

In [87]:
zipcodes_geo = gpd.read_file('/Users/k.simmons/Desktop/NSS/data analytics bootcamp/capstone/Data/zipcodes.geojson')

In [92]:
zipcodes_geo.head()

zip objectid    po_name      shape_stlength        shape_starea  \
0  37115        1    MADISON  178783.02488886821  596553400.57885742   
1  37216        3  NASHVILLE  75820.997821400058  188884682.28344727   
2  37204        9  NASHVILLE  93180.292250425613  200664795.51708984   
3  37027       11  BRENTWOOD   159760.6942933173  174978422.04101562   
4  37064       18   FRANKLIN  28995.828320601937  46969608.005737305   

                                            geometry  
0  MULTIPOLYGON (((-86.68725 36.31821, -86.68722 ...  
1  MULTIPOLYGON (((-86.73451 36.23774, -86.73425 ...  
2  MULTIPOLYGON (((-86.77914 36.13424, -86.77923 ...  
3  MULTIPOLYGON (((-86.81258 36.06319, -86.81263 ...  
4  MULTIPOLYGON (((-87.02197 36.01200, -87.02140 ...

# creating list of zipcodes that are contained within Nashville city limits (not entire Metro Nashville-Davidson County)

In [93]:
nashmask = zipcodes_geo['po_name'].isin(['NASHVILLE'])

In [94]:
nashzips = zipcodes_geo[nashmask].reset_index(drop=True)

37207 is listed twice in the geodata, because the zipcode is split geographically. To avoid key:value issues later on, I am eliminating the smaller 37207 polygon.

In [95]:
drop49 = nashzips['objectid'].isin(['49'])

In [96]:
nashzips[drop49]

zip objectid    po_name      shape_stlength        shape_starea  \
7  37207       49  NASHVILLE  14456.130686344946  6987521.0933837891   

                                            geometry  
7  MULTIPOLYGON (((-86.78596 36.29097, -86.78595 ...

In [97]:
nashzips = nashzips.drop(index=7)

In [195]:
list = list(nashzips['zip'])

In [196]:
list

['37216',
 '37204',
 '37221',
 '37212',
 '37209',
 '37206',
 '37217',
 '37219',
 '37218',
 '37232',
 '37213',
 '37205',
 '37203',
 '37201',
 '37214',
 '37240',
 '37208',
 '37207',
 '37215',
 '37228',
 '37210',
 '37211',
 '37220']

doublechecking that I only retained the larger of the two polygons

In [99]:
nash37207 = nashzips['zip'].isin(['37207'])

In [100]:
nashzips[nash37207]

zip objectid    po_name      shape_stlength        shape_starea  \
18  37207       48  NASHVILLE  196775.60104082408  556772811.32653809   

                                             geometry  
18  MULTIPOLYGON (((-86.75459 36.29021, -86.75465 ...

In [101]:
#nashzips.to_excel('nashzipcodes.xlsx')

In [102]:
polygon37216 = nashzips.loc[nashzips['zip'] == '37216']
polygon37204 = nashzips.loc[nashzips['zip'] == '37204']
polygon37221 = nashzips.loc[nashzips['zip'] == '37221']
polygon37212 = nashzips.loc[nashzips['zip'] == '37212']
polygon37209 = nashzips.loc[nashzips['zip'] == '37209']
polygon37206 = nashzips.loc[nashzips['zip'] == '37206']
polygon37217 = nashzips.loc[nashzips['zip'] == '37217']
polygon37207 = nashzips.loc[nashzips['zip'] == '37207']
polygon37219 = nashzips.loc[nashzips['zip'] == '37219']
polygon37218 = nashzips.loc[nashzips['zip'] == '37218']
polygon37232 = nashzips.loc[nashzips['zip'] == '37232']
polygon37213 = nashzips.loc[nashzips['zip'] == '37213']
polygon37205 = nashzips.loc[nashzips['zip'] == '37205']
polygon37203 = nashzips.loc[nashzips['zip'] == '37203']
polygon37201 = nashzips.loc[nashzips['zip'] == '37201']
polygon37214 = nashzips.loc[nashzips['zip'] == '37214']
polygon37240 = nashzips.loc[nashzips['zip'] == '37240']
polygon37208 = nashzips.loc[nashzips['zip'] == '37208']
polygon37215 = nashzips.loc[nashzips['zip'] == '37215']
polygon37228 = nashzips.loc[nashzips['zip'] == '37228']
polygon37210 = nashzips.loc[nashzips['zip'] == '37210']
polygon37211 = nashzips.loc[nashzips['zip'] == '37211']
polygon37220 = nashzips.loc[nashzips['zip'] == '37220']

# creating centroid for each Nashville zipcode, to aid in Google API queries

In [15]:
center37216 = polygon37216.geometry.centroid
center37204 = polygon37204.geometry.centroid
center37221 = polygon37221.geometry.centroid
center37212 = polygon37212.geometry.centroid
center37209 = polygon37209.geometry.centroid
center37206 = polygon37206.geometry.centroid
center37217 = polygon37217.geometry.centroid
center37207 = polygon37207.geometry.centroid
center37219 = polygon37219.geometry.centroid
center37218 = polygon37218.geometry.centroid
center37232 = polygon37232.geometry.centroid
center37213 = polygon37213.geometry.centroid
center37205 = polygon37205.geometry.centroid
center37203 = polygon37203.geometry.centroid
center37201 = polygon37201.geometry.centroid
center37214 = polygon37214.geometry.centroid
center37240 = polygon37240.geometry.centroid
center37208 = polygon37208.geometry.centroid
center37215 = polygon37215.geometry.centroid
center37228 = polygon37228.geometry.centroid
center37210 = polygon37210.geometry.centroid
center37211 = polygon37211.geometry.centroid
center37220 = polygon37220.geometry.centroid

/var/folders/s3/87cx_4f97x52rgnl47c9skpr0000gn/T/ipykernel_69616/3432679964.py:1: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  center37216 = polygon37216.geometry.centroid
/var/folders/s3/87cx_4f97x52rgnl47c9skpr0000gn/T/ipykernel_69616/3432679964.py:2: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  center37204 = polygon37204.geometry.centroid
/var/folders/s3/87cx_4f97x52rgnl47c9skpr0000gn/T/ipykernel_69616/3432679964.py:3: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  center37221 = polygon37221.geometry.centroid
/var/folders/s3/87cx_4f97x52rgnl47c9skpr0000gn/T/ipykernel

# creating list of LAT/LONG of each Zipcode's centroid, for inclusion in Google API query

In [16]:
center37207

18    POINT (-86.77677 36.23245)
dtype: geometry

In [17]:
print(center37216[0])

POINT (-86.7263455721062 36.21605012332708)


In [104]:
latlng37216 = f'{center37216[0].y},{center37216[0].x}'
latlng37204 = f'{center37204[1].y},{center37204[1].x}'
latlng37221 = f'{center37221[2].y},{center37221[2].x}'
latlng37212 = f'{center37212[3].y},{center37212[3].x}'
latlng37209 = f'{center37209[4].y},{center37209[4].x}'
latlng37206 = f'{center37206[5].y},{center37206[5].x}'
latlng37217 = f'{center37217[6].y},{center37217[6].x}'
latlng37219 = f'{center37219[8].y},{center37219[8].x}'
latlng37218 = f'{center37218[9].y},{center37218[9].x}'
latlng37232 = f'{center37232[10].y},{center37232[10].x}'
latlng37213 = f'{center37213[11].y},{center37213[11].x}'
latlng37205 = f'{center37205[12].y},{center37205[12].x}'
latlng37203 = f'{center37203[13].y},{center37203[13].x}'
latlng37201 = f'{center37201[14].y},{center37201[14].x}'
latlng37214 = f'{center37214[15].y},{center37214[15].x}'
latlng37240 = f'{center37240[16].y},{center37240[16].x}'
latlng37208 = f'{center37208[17].y},{center37208[17].x}'
latlng37207 = f'{center37207[18].y},{center37207[18].x}'
latlng37215 = f'{center37215[19].y},{center37215[19].x}'
latlng37228 = f'{center37228[20].y},{center37228[20].x}'
latlng37210 = f'{center37210[21].y},{center37210[21].x}'
latlng37211 = f'{center37211[22].y},{center37211[22].x}'
latlng37220 = f'{center37220[23].y},{center37220[23].x}'

In [105]:
latlng37207

'36.23245257407244,-86.77676762469858'

In [106]:
type(''.join(latlng37207))

str

In [107]:
type(latlng37207)

str

# made Nashville zipcode boundary map for my own visualization purposes while in workflow

In [108]:
nash_center37203 = center37203.geometry.centroid[13]

/var/folders/s3/87cx_4f97x52rgnl47c9skpr0000gn/T/ipykernel_69616/1914074261.py:1: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  nash_center37203 = center37203.geometry.centroid[13]


In [111]:
print(nash_center37203)

POINT (-86.78898899667411 36.14860232841574)


In [112]:
nash_center = [nash_center37203.y, nash_center37203.x]
print(nash_center)

[36.14860232841574, -86.7889889966741]


In [113]:
nash_map = folium.Map(location = nash_center, zoom_start = 10)
plugins.MeasureControl().add_to(nash_map)

In [114]:
nash_map

In [115]:
folium.GeoJson(polygon37216).add_to(nash_map)
folium.GeoJson(polygon37204).add_to(nash_map)
folium.GeoJson(polygon37221).add_to(nash_map)
folium.GeoJson(polygon37212).add_to(nash_map)
folium.GeoJson(polygon37209).add_to(nash_map)
folium.GeoJson(polygon37206).add_to(nash_map)
folium.GeoJson(polygon37217).add_to(nash_map)
folium.GeoJson(polygon37207).add_to(nash_map)
folium.GeoJson(polygon37219).add_to(nash_map)
folium.GeoJson(polygon37218).add_to(nash_map)
folium.GeoJson(polygon37232).add_to(nash_map)
folium.GeoJson(polygon37213).add_to(nash_map)
folium.GeoJson(polygon37205).add_to(nash_map)
folium.GeoJson(polygon37203).add_to(nash_map)
folium.GeoJson(polygon37201).add_to(nash_map)
folium.GeoJson(polygon37214).add_to(nash_map)
folium.GeoJson(polygon37240).add_to(nash_map)
folium.GeoJson(polygon37208).add_to(nash_map)
folium.GeoJson(polygon37215).add_to(nash_map)
folium.GeoJson(polygon37228).add_to(nash_map)
folium.GeoJson(polygon37210).add_to(nash_map)
folium.GeoJson(polygon37211).add_to(nash_map)
folium.GeoJson(polygon37220).add_to(nash_map)


In [116]:
nash_map

# there are 23 zipcodes within Nashville city limits to do queries for

# beginning of queries for supermarkets/grocers using lat/lng centroids for each zipcode

37204 supermarkets/grocers, 2000 meter radius

In [182]:
#grocery_stores37204 = []
#params37204 = {}

#endpoint_url37204 = "https://maps.googleapis.com/maps/api/place/textsearch/json?query=grocery+store+in+37204&location=36.10566266613879,-86.7746655408201&radius=2000&region=us&type=grocery_or_supermarket,supermarket,bakery,food&key={api_key}"

#res37204 = requests.get(endpoint_url37204, params = params37204)
#results37204 = json.loads(res37204.content)
#grocery_stores37204.extend(results37204['results'])
#time.sleep(2)
#while "next_page_token" in results37204:
   # params37204['pagetoken'] = results37204['next_page_token'],
   # res37204 = requests.get(endpoint_url37204, params = params37204)
   # results37204 = json.loads(res37204.content)
   # grocery_stores37204.extend(results37204['results'])
   # time.sleep(2)'''

In [183]:
#res37204

In [184]:
#results37204

In [185]:
#shop_name37204 = []
#formatted_address37204 = []
#shop_lat37204 = []
#shop_lng37204 = []

#for i in range(len(grocery_stores37204)):
    #shop37204 = grocery_stores37204[i]

   # try:
    #    shop_name37204.append(shop37204['name'])
   # except:
  #      shop_name37204.append('none')

  #  try:
  #      formatted_address37204.append(shop37204['formatted_address'])
 #   except:
  #      formatted_address37204.append('none')

  #  try:
  #      shop_lat37204.append(shop37204['geometry']['location']['lat'])
  #  except:
   #     shop_lat37204.append('none')

   # try:
   #     shop_lng37204.append(shop37204['geometry']['location']['lng'])
   # except:
    #    shop_lng37204.append('none')

In [186]:
#df_dict37204 = {'shop_name':shop_name37204, 'shop_address':formatted_address37204, 'shop_lat':shop_lat37204, 'shop_lng':shop_lng37204}

#grocery_stores37204_df = pd.DataFrame(df_dict37204)

#grocery_stores37204_df['duplicator'] = grocery_stores37204_df['shop_name'] + grocery_stores37204_df['shop_address']

#grocery_stores37204_df.drop_duplicates(['duplicator'], inplace=True)

In [187]:
#grocery_stores37204_df

37221 supermarkets/grocers, 8000 meter radius

In [188]:
#grocery_stores37221 = []
#params37221 = {}

#endpoint_url37221 = "https://maps.googleapis.com/maps/api/place/textsearch/json?query=grocery+store+in+37221&location=36.06283153351842,-86.97531387608755&radius=8000&region=us&type=grocery_or_supermarket,supermarket,bakery,food&key={api_key}"

#res37221 = requests.get(endpoint_url37221, params = params37221)
#results37221 = json.loads(res37221.content)
#grocery_stores37221.extend(results37221['results'])
#time.sleep(2)
#while "next_page_token" in results37221:
    #params37221['pagetoken'] = results37221['next_page_token'],
    #res37221 = requests.get(endpoint_url37221, params = params37221)
    #results37221 = json.loads(res37221.content)
   # grocery_stores37221.extend(results37221['results'])
   # time.sleep(2)

In [189]:
#res37221

In [190]:
#results37221

In [191]:
#shop_name37221 = []
#formatted_address37221 = []
#shop_lat37221 = []
#shop_lng37221 = []

#for i in range(len(grocery_stores37221)):
   # shop37221 = grocery_stores37221[i]

   # try:
   #     shop_name37221.append(shop37221['name'])
   # except:
  #      shop_name37221.append('none')

  #  try:
  #      formatted_address37221.append(shop37221['formatted_address'])
  #  except:
  #      formatted_address37221.append('none')

   # try:
  #      shop_lat37221.append(shop37221['geometry']['location']['lat'])
   # except:
   #     shop_lat37221.append('none')

  #  try:
  #      shop_lng37221.append(shop37221['geometry']['location']['lng'])
 #   except:
  #      shop_lng37221.append('none')

In [192]:
#df_dict37221 = {'shop_name':shop_name37221, 'shop_address':formatted_address37221, 'shop_lat':shop_lat37221, 'shop_lng':shop_lng37221}

#grocery_stores37221_df = pd.DataFrame(df_dict37221)

#grocery_stores37221_df['duplicator'] = grocery_stores37221_df['shop_name'] + grocery_stores37221_df['shop_address']

#grocery_stores37221_df.drop_duplicates(['duplicator'], inplace=True)

In [193]:
#grocery_stores37221_df

37212 supermarkets/grocers, 8000 meter radius

In [194]:
#grocery_stores37212 = []
##params37212 = {}

#endpoint_url37212 = "https://maps.googleapis.com/maps/api/place/textsearch/json?query=grocery+store+in+37212&location=36.133345610650146,-86.80157366719409&radius=8000&region=us&type=grocery_or_supermarket,supermarket,bakery,food&key={api_key}"

#res37212 = requests.get(endpoint_url37212, params = params37212)
##results37212 = json.loads(res37212.content)
#grocery_stores37212.extend(results37212['results'])
#time.sleep(2)
#while "next_page_token" in results37212:
    #params37212['pagetoken'] = results37212['next_page_token'],
   # res37212 = requests.get(endpoint_url37212, params = params37212)
    #results37212 = json.loads(res37212.content)
   # grocery_stores37212.extend(results37212['results'])
   # time.sleep(2)

In [195]:
#res37212

In [196]:
#results37212

In [197]:
#shop_name37212 = []
#formatted_address37212 = []
#shop_lat37212 = []
#shop_lng37212 = []

#for i in range(len(grocery_stores37212)):
  #  shop37212 = grocery_stores37212[i]

 #   try:
 #       shop_name37212.append(shop37212['name'])
 #   except:
#        shop_name37212.append('none')

##    try:
 #       formatted_address37212.append(shop37212['formatted_address'])
 #   except:
  #      formatted_address37212.append('none')

 #   try:
 #       shop_lat37212.append(shop37212['geometry']['location']['lat'])
 #   except:
  #      shop_lat37212.append('none')

  #  try:
  #      shop_lng37212.append(shop37212['geometry']['location']['lng'])
   # except:
  #      shop_lng37212.append('none')

In [198]:
#df_dict37212 = {'shop_name':shop_name37212, 'shop_address':formatted_address37212, 'shop_lat':shop_lat37212, 'shop_lng':shop_lng37212}

#grocery_stores37212_df = pd.DataFrame(df_dict37212)

#grocery_stores37212_df['duplicator'] = grocery_stores37212_df['shop_name'] + grocery_stores37212_df['shop_address']

#grocery_stores37212_df.drop_duplicates(['duplicator'], inplace=True)

In [199]:
#grocery_stores37212_df

In [200]:
#usedzips = nashzips['zip']
#usedzips = usedzips.tolist()

In [201]:
#usedzips

# function dictionaries

creating dictionary with approximate measurement of longest width of zipcode, to be halved for Places API radius parameter.

In [29]:
zipradius = {'radius37216' : str(6424/2),          
             'radius37204' : str(4413/2),
             'radius37221' : str(14868/2),
             'radius37212' : str(3617/2),
             'radius37209' : str(16250/2),
             'radius37206' : str(7317/2),
             'radius37217' : str(12820/2),
             'radius37207' : str(12584/2),
             'radius37219' : str(1536/2),
             'radius37218' : str(15417/2),
             'radius37232' : str(803/2),
             'radius37213' : str(2961/2),
             'radius37205' : str(10009/2),
             'radius37203' : str(5827/2),
             'radius37201' : str(2193/2),
             'radius37214' : str(15907/2),
             'radius37240' : str(540/2),
             'radius37208' : str(5053/2),
             'radius37215' : str(8832/2),
             'radius37228' : str(3798/2),
             'radius37210' : str(6575/2),
             'radius37211' : str(14141/2),
             'radius37220' : str(6084/2),
           }

finally, now using the lists I made to create a dictionary of the centroid coordinates

In [117]:
coord_dict = {'coord37216' : ''.join(latlng37216),
              'coord37204' : ''.join(latlng37204),
              'coord37221' : ''.join(latlng37221),
              'coord37212' : ''.join(latlng37212),
              'coord37209' : ''.join(latlng37209),
              'coord37206' : ''.join(latlng37206),
              'coord37217' : ''.join(latlng37217),
              'coord37207' : ''.join(latlng37207),
              'coord37219' : ''.join(latlng37219),
              'coord37218' : ''.join(latlng37218),
              'coord37232' : ''.join(latlng37232),
              'coord37213' : ''.join(latlng37213),
              'coord37205' : ''.join(latlng37205),
              'coord37203' : ''.join(latlng37203),
              'coord37201' : ''.join(latlng37201),
              'coord37214' : ''.join(latlng37214),
              'coord37240' : ''.join(latlng37240),
              'coord37208' : ''.join(latlng37208),
              'coord37215' : ''.join(latlng37215),
              'coord37228' : ''.join(latlng37228),
              'coord37210' : ''.join(latlng37210),
              'coord37211' : ''.join(latlng37211),
              'coord37220' : ''.join(latlng37220),
             }

creating a combined dictionary from the prior two dictionaries

In [118]:
zip_codes = { int(zip_code.replace("radius", "")): { "radius": zipradius[zip_code], } for zip_code in zipradius }
for zip_code in zip_codes:
    zip_codes[zip_code]["coord"] = coord_dict[f"coord{zip_code}"]

In [205]:
#len(zip_codes)

In [45]:
#len(coord_dict)

In [207]:
#len(zipradius)

# okay, manually changing the query code by copy/pasting the zipcode many times is much too tedious, drawn out, and prone to error. Time to call in the query function:

supermarket/grocery query function:

In [279]:
def grocery_query(zip, coord_dict, zipradius):
    grocery_stores = []

    params = { 
            "query": f"grocery+in+{zip}",
            "location": coord_dict,
            "address": f"zipcode {zip}",
            "radius": zipradius,
            "region": "us",
            "type": "grocery_or_supermarket,supermarket",
            "key": config.api_key,
            }

    endpoint_url= "https://maps.googleapis.com/maps/api/place/textsearch/json"

    res = requests.get(endpoint_url, params = params)
    results = res.json()
    grocery_stores.extend(results['results'])
    time.sleep(2)
    while "next_page_token" in results:
        params['pagetoken'] = results['next_page_token'],
        res = requests.get(endpoint_url, params = params)
        results = json.loads(res.content)
        grocery_stores.extend(results['results'])
        time.sleep(2)

    shop_name = []
    formatted_address = []
    shop_lat = []
    shop_lng = []
    type = []

    for i in range(len(grocery_stores)):
        shop = grocery_stores[i]

        try:
            shop_name.append(shop['name'])
        except:
            shop_name.append('none')

        try:
            formatted_address.append(shop['formatted_address'])
        except:
            formatted_address.append('none')

        try:
            shop_lat.append(shop['geometry']['location']['lat'])
        except:
            shop_lat.append('none')

        try:
            shop_lng.append(shop['geometry']['location']['lng'])
        except:
            shop_lng.append('none')
        
        try:
            type.append(shop['types'])
        except:
            type.append('none')

    df_dict = {'shop_name':shop_name, 'shop_address':formatted_address, 'shop_lat':shop_lat, 'shop_lng':shop_lng, 'types':type}

    grocery_stores = pd.DataFrame(df_dict)

    #grocery_stores.to_csv(f'Data/API_queries/grocery/grocery_stores{zip}.csv')

    return grocery_stores

    

gas station query function:

In [280]:
def gasstation_query(zip, coord_dict, zipradius):
    gas_stations= []

    params = { 
            "query": f"gas+station+in+{zip}",
            "location": coord_dict,
            "address": f"zipcode {zip}",
            "radius": zipradius,
            "region": "us",
            "type": "gas_station",
            "key": config.api_key,
            }

    endpoint_url= "https://maps.googleapis.com/maps/api/place/textsearch/json"

    res = requests.get(endpoint_url, params = params)
    results = res.json()
    gas_stations.extend(results['results'])
    time.sleep(2)
    while "next_page_token" in results:
        params['pagetoken'] = results['next_page_token'],
        res = requests.get(endpoint_url, params = params)
        results = json.loads(res.content)
        gas_stations.extend(results['results'])
        time.sleep(2)

    shop_name = []
    formatted_address = []
    shop_lat = []
    shop_lng = []
    type = []

    for i in range(len(gas_stations)):
        shop = gas_stations[i]

        try:
            shop_name.append(shop['name'])
        except:
            shop_name.append('none')

        try:
            formatted_address.append(shop['formatted_address'])
        except:
            formatted_address.append('none')

        try:
            shop_lat.append(shop['geometry']['location']['lat'])
        except:
            shop_lat.append('none')

        try:
            shop_lng.append(shop['geometry']['location']['lng'])
        except:
            shop_lng.append('none')
        
        try:
            type.append(shop['types'])
        except:
            type.append('none')

    df_dict = {'shop_name':shop_name, 'shop_address':formatted_address, 'shop_lat':shop_lat, 'shop_lng':shop_lng, 'types':type}

    gas_stations = pd.DataFrame(df_dict)

    #gas_stations.to_csv(f'Data/API_queries/gas_station/gas_stations{zip}.csv')

    return gas_stations


convenience store query

In [281]:
def convstore_query(zip, coord_dict, zipradius):
    convenience_store= []

    params = { 
            "query": f"convenience+store+in+{zip}",
            "location": coord_dict,
            "address": f"zipcode {zip}",
            "radius": zipradius,
            "region": "us",
            "type": "convenience_store",
            "key": config.api_key,
            }

    endpoint_url= "https://maps.googleapis.com/maps/api/place/textsearch/json"

    res = requests.get(endpoint_url, params = params)
    results = res.json()
    convenience_store.extend(results['results'])
    time.sleep(2)
    while "next_page_token" in results:
        params['pagetoken'] = results['next_page_token'],
        res = requests.get(endpoint_url, params = params)
        results = json.loads(res.content)
        convenience_store.extend(results['results'])
        time.sleep(2)

    shop_name = []
    formatted_address = []
    shop_lat = []
    shop_lng = []
    type = []

    for i in range(len(convenience_store)):
        shop = convenience_store[i]

        try:
            shop_name.append(shop['name'])
        except:
            shop_name.append('none')

        try:
            formatted_address.append(shop['formatted_address'])
        except:
            formatted_address.append('none')

        try:
            shop_lat.append(shop['geometry']['location']['lat'])
        except:
            shop_lat.append('none')

        try:
            shop_lng.append(shop['geometry']['location']['lng'])
        except:
            shop_lng.append('none')
        
        try:
            type.append(shop['types'])
        except:
            type.append('none')

    df_dict = {'shop_name':shop_name, 'shop_address':formatted_address, 'shop_lat':shop_lat, 'shop_lng':shop_lng, 'types':type}

    convenience_store = pd.DataFrame(df_dict)

    #convenience_store.to_csv(f'Data/API_queries/convenience_store/convenience_store{zip}.csv')

    return convenience_store


restaurant query function:

In [282]:
def restaurant_query(zip, coord_dict, zipradius):
    restaurants= []

    params = { 
            "query": f"restaurant+in+{zip}",
            "location": coord_dict,
            "address": f"zipcode {zip}",
            "radius": zipradius,
            "region": "us",
            "type": "restaurant, cafe",
            "key": config.api_key,
            }

    endpoint_url= "https://maps.googleapis.com/maps/api/place/textsearch/json"

    res = requests.get(endpoint_url, params = params)
    results = res.json()
    restaurants.extend(results['results'])
    time.sleep(2)
    while "next_page_token" in results:
        params['pagetoken'] = results['next_page_token'],
        res = requests.get(endpoint_url, params = params)
        results = json.loads(res.content)
        restaurants.extend(results['results'])
        time.sleep(2)

    shop_name = []
    formatted_address = []
    shop_lat = []
    shop_lng = []
    type = []

    for i in range(len(restaurants)):
        shop = restaurants[i]

        try:
            shop_name.append(shop['name'])
        except:
            shop_name.append('none')

        try:
            formatted_address.append(shop['formatted_address'])
        except:
            formatted_address.append('none')

        try:
            shop_lat.append(shop['geometry']['location']['lat'])
        except:
            shop_lat.append('none')

        try:
            shop_lng.append(shop['geometry']['location']['lng'])
        except:
            shop_lng.append('none')
        
        try:
            type.append(shop['types'])
        except:
            type.append('none')

    df_dict = {'shop_name':shop_name, 'shop_address':formatted_address, 'shop_lat':shop_lat, 'shop_lng':shop_lng, 'types':type}

    restaurants = pd.DataFrame(df_dict)

    #restaurants.to_csv(f'Data/API_queries/restaurant/restaurants{zip}.csv')

    return restaurants


kroger query:

In [283]:
def kroger_query(zip, coord_dict, zipradius):
    kroger= []

    params = { 
            "query": f"Kroger+in+{zip}",
            "location": coord_dict,
            "address": f"zipcode {zip}",
            "radius": zipradius,
            "region": "us",
            "type": "grocery_or_supermarket,supermarket",
            "key": config.api_key,
            }

    endpoint_url= "https://maps.googleapis.com/maps/api/place/textsearch/json"

    res = requests.get(endpoint_url, params = params)
    results = res.json()
    kroger.extend(results['results'])
    time.sleep(2)
    while "next_page_token" in results:
        params['pagetoken'] = results['next_page_token'],
        res = requests.get(endpoint_url, params = params)
        results = json.loads(res.content)
        kroger.extend(results['results'])
        time.sleep(2)

    shop_name = []
    formatted_address = []
    shop_lat = []
    shop_lng = []
    type = []

    for i in range(len(kroger)):
        shop = kroger[i]

        try:
            shop_name.append(shop['name'])
        except:
            shop_name.append('none')

        try:
            formatted_address.append(shop['formatted_address'])
        except:
            formatted_address.append('none')

        try:
            shop_lat.append(shop['geometry']['location']['lat'])
        except:
            shop_lat.append('none')

        try:
            shop_lng.append(shop['geometry']['location']['lng'])
        except:
            shop_lng.append('none')
        
        try:
            type.append(shop['types'])
        except:
            type.append('none')

    df_dict = {'shop_name':shop_name, 'shop_address':formatted_address, 'shop_lat':shop_lat, 'shop_lng':shop_lng, 'types':type}

    kroger = pd.DataFrame(df_dict)

    #kroger.to_csv(f'Data/API_queries/grocery/kroger/kroger{zip}.csv')

    return kroger


Publix query:

In [284]:
def publix_query(zip, coord_dict, zipradius):
    publix= []

    params = { 
            "query": f"publix+in+{zip}",
            "location": coord_dict,
            "address": f"zipcode {zip}",
            "radius": zipradius,
            "region": "us",
            "type": "grocery_or_supermarket,supermarket",
            "key": config.api_key,
            }

    endpoint_url= "https://maps.googleapis.com/maps/api/place/textsearch/json"

    res = requests.get(endpoint_url, params = params)
    results = res.json()
    publix.extend(results['results'])
    time.sleep(2)
    while "next_page_token" in results:
        params['pagetoken'] = results['next_page_token'],
        res = requests.get(endpoint_url, params = params)
        results = json.loads(res.content)
        publix.extend(results['results'])
        time.sleep(2)

    shop_name = []
    formatted_address = []
    shop_lat = []
    shop_lng = []
    type = []

    for i in range(len(publix)):
        shop = publix[i]

        try:
            shop_name.append(shop['name'])
        except:
            shop_name.append('none')

        try:
            formatted_address.append(shop['formatted_address'])
        except:
            formatted_address.append('none')

        try:
            shop_lat.append(shop['geometry']['location']['lat'])
        except:
            shop_lat.append('none')

        try:
            shop_lng.append(shop['geometry']['location']['lng'])
        except:
            shop_lng.append('none')
        
        try:
            type.append(shop['types'])
        except:
            type.append('none')

    df_dict = {'shop_name':shop_name, 'shop_address':formatted_address, 'shop_lat':shop_lat, 'shop_lng':shop_lng, 'types':type}

    publix = pd.DataFrame(df_dict)

    #publix.to_csv(f'Data/API_queries/grocery/publix/publix{zip}.csv')

    return publix


Walmart Query:

In [285]:
def walmart_query(zip, coord_dict, zipradius):
    walmart= []

    params = { 
            "query": f"walmart+in+{zip}",
            "location": coord_dict,
            "address": f"zipcode {zip}",
            "radius": zipradius,
            "region": "us",
            "type": "grocery_or_supermarket,supermarket",
            "key": config.api_key,
            }

    endpoint_url= "https://maps.googleapis.com/maps/api/place/textsearch/json"

    res = requests.get(endpoint_url, params = params)
    results = res.json()
    walmart.extend(results['results'])
    time.sleep(2)
    while "next_page_token" in results:
        params['pagetoken'] = results['next_page_token'],
        res = requests.get(endpoint_url, params = params)
        results = json.loads(res.content)
        walmart.extend(results['results'])
        time.sleep(2)

    shop_name = []
    formatted_address = []
    shop_lat = []
    shop_lng = []
    type = []

    for i in range(len(walmart)):
        shop = walmart[i]

        try:
            shop_name.append(shop['name'])
        except:
            shop_name.append('none')

        try:
            formatted_address.append(shop['formatted_address'])
        except:
            formatted_address.append('none')

        try:
            shop_lat.append(shop['geometry']['location']['lat'])
        except:
            shop_lat.append('none')

        try:
            shop_lng.append(shop['geometry']['location']['lng'])
        except:
            shop_lng.append('none')
        
        try:
            type.append(shop['types'])
        except:
            type.append('none')

    df_dict = {'shop_name':shop_name, 'shop_address':formatted_address, 'shop_lat':shop_lat, 'shop_lng':shop_lng, 'types':type}

    walmart = pd.DataFrame(df_dict)

    #walmart.to_csv(f'Data/API_queries/grocery/walmart/walmart{zip}.csv')

    return walmart


ALDI query:

In [286]:
def ALDI_query(zip, coord_dict, zipradius):
    ALDI= []

    params = { 
            "query": f"ALDI+in+{zip}",
            "location": coord_dict,
            "address": f"zipcode {zip}",
            "radius": zipradius,
            "region": "us",
            "type": "grocery_or_supermarket,supermarket",
            "key": config.api_key,
            }

    endpoint_url= "https://maps.googleapis.com/maps/api/place/textsearch/json"

    res = requests.get(endpoint_url, params = params)
    results = res.json()
    ALDI.extend(results['results'])
    time.sleep(2)
    while "next_page_token" in results:
        params['pagetoken'] = results['next_page_token'],
        res = requests.get(endpoint_url, params = params)
        results = json.loads(res.content)
        ALDI.extend(results['results'])
        time.sleep(2)

    shop_name = []
    formatted_address = []
    shop_lat = []
    shop_lng = []
    type = []

    for i in range(len(ALDI)):
        shop = ALDI[i]

        try:
            shop_name.append(shop['name'])
        except:
            shop_name.append('none')

        try:
            formatted_address.append(shop['formatted_address'])
        except:
            formatted_address.append('none')

        try:
            shop_lat.append(shop['geometry']['location']['lat'])
        except:
            shop_lat.append('none')

        try:
            shop_lng.append(shop['geometry']['location']['lng'])
        except:
            shop_lng.append('none')
        
        try:
            type.append(shop['types'])
        except:
            type.append('none')

    df_dict = {'shop_name':shop_name, 'shop_address':formatted_address, 'shop_lat':shop_lat, 'shop_lng':shop_lng, 'types':type}

    ALDI = pd.DataFrame(df_dict)

    #ALDI.to_csv(f'Data/API_queries/grocery/ALDI/ALDI{zip}.csv')

    return ALDI


Piggly Wiggly query:

In [287]:
def piggly_wiggly_query(zip, coord_dict, zipradius):
    piggly_wiggly= []

    params = { 
            "query": f"piggly+wiggly+in+{zip}",
            "location": coord_dict,
            "address": f"zipcode {zip}",
            "radius": zipradius,
            "region": "us",
            "type": "grocery_or_supermarket,supermarket",
            "key": config.api_key,
            }

    endpoint_url= "https://maps.googleapis.com/maps/api/place/textsearch/json"

    res = requests.get(endpoint_url, params = params)
    results = res.json()
    piggly_wiggly.extend(results['results'])
    time.sleep(2)
    while "next_page_token" in results:
        params['pagetoken'] = results['next_page_token'],
        res = requests.get(endpoint_url, params = params)
        results = json.loads(res.content)
        piggly_wiggly.extend(results['results'])
        time.sleep(2)

    shop_name = []
    formatted_address = []
    shop_lat = []
    shop_lng = []
    type = []

    for i in range(len(piggly_wiggly)):
        shop = piggly_wiggly[i]

        try:
            shop_name.append(shop['name'])
        except:
            shop_name.append('none')

        try:
            formatted_address.append(shop['formatted_address'])
        except:
            formatted_address.append('none')

        try:
            shop_lat.append(shop['geometry']['location']['lat'])
        except:
            shop_lat.append('none')

        try:
            shop_lng.append(shop['geometry']['location']['lng'])
        except:
            shop_lng.append('none')
        
        try:
            type.append(shop['types'])
        except:
            type.append('none')

    df_dict = {'shop_name':shop_name, 'shop_address':formatted_address, 'shop_lat':shop_lat, 'shop_lng':shop_lng, 'types':type}

    piggly_wiggly = pd.DataFrame(df_dict)

    #piggly_wiggly.to_csv(f'Data/API_queries/grocery/piggly_wiggly/piggly_wiggly{zip}.csv')

    return piggly_wiggly


Turnip Truck query:

In [288]:
def turnip_truck_query(zip, coord_dict, zipradius):
    turnip_truck= []

    params = { 
            "query": f"turnip+truck+in+{zip}",
            "location": coord_dict,
            "address": f"zipcode {zip}",
            "radius": zipradius,
            "region": "us",
            "type": "grocery_or_supermarket,supermarket",
            "key": config.api_key,
            }

    endpoint_url= "https://maps.googleapis.com/maps/api/place/textsearch/json"

    res = requests.get(endpoint_url, params = params)
    results = res.json()
    turnip_truck.extend(results['results'])
    time.sleep(2)
    while "next_page_token" in results:
        params['pagetoken'] = results['next_page_token'],
        res = requests.get(endpoint_url, params = params)
        results = json.loads(res.content)
        turnip_truck.extend(results['results'])
        time.sleep(2)

    shop_name = []
    formatted_address = []
    shop_lat = []
    shop_lng = []
    type = []

    for i in range(len(turnip_truck)):
        shop = turnip_truck[i]

        try:
            shop_name.append(shop['name'])
        except:
            shop_name.append('none')

        try:
            formatted_address.append(shop['formatted_address'])
        except:
            formatted_address.append('none')

        try:
            shop_lat.append(shop['geometry']['location']['lat'])
        except:
            shop_lat.append('none')

        try:
            shop_lng.append(shop['geometry']['location']['lng'])
        except:
            shop_lng.append('none')
        
        try:
            type.append(shop['types'])
        except:
            type.append('none')

    df_dict = {'shop_name':shop_name, 'shop_address':formatted_address, 'shop_lat':shop_lat, 'shop_lng':shop_lng, 'types':type}

    turnip_truck = pd.DataFrame(df_dict)

    #turnip_truck.to_csv(f'Data/API_queries/grocery/turnip_truck/turnip_truck{zip}.csv')

    return turnip_truck


Whole Foods query:

In [289]:
def whole_foods_query(zip, coord_dict, zipradius):
    whole_foods= []

    params = { 
            "query": f"whole+foods+in+{zip}",
            "location": coord_dict,
            "address": f"zipcode {zip}",
            "radius": zipradius,
            "region": "us",
            "type": "grocery_or_supermarket,supermarket",
            "key": config.api_key,
            }

    endpoint_url= "https://maps.googleapis.com/maps/api/place/textsearch/json"

    res = requests.get(endpoint_url, params = params)
    results = res.json()
    whole_foods.extend(results['results'])
    time.sleep(2)
    while "next_page_token" in results:
        params['pagetoken'] = results['next_page_token'],
        res = requests.get(endpoint_url, params = params)
        results = json.loads(res.content)
        whole_foods.extend(results['results'])
        time.sleep(2)

    shop_name = []
    formatted_address = []
    shop_lat = []
    shop_lng = []
    type = []

    for i in range(len(whole_foods)):
        shop = whole_foods[i]

        try:
            shop_name.append(shop['name'])
        except:
            shop_name.append('none')

        try:
            formatted_address.append(shop['formatted_address'])
        except:
            formatted_address.append('none')

        try:
            shop_lat.append(shop['geometry']['location']['lat'])
        except:
            shop_lat.append('none')

        try:
            shop_lng.append(shop['geometry']['location']['lng'])
        except:
            shop_lng.append('none')
        
        try:
            type.append(shop['types'])
        except:
            type.append('none')

    df_dict = {'shop_name':shop_name, 'shop_address':formatted_address, 'shop_lat':shop_lat, 'shop_lng':shop_lng, 'types':type}

    whole_foods = pd.DataFrame(df_dict)

    #whole_foods.to_csv(f'Data/API_queries/grocery/whole_foods/whole_foods{zip}.csv')

    return whole_foods


Trader Joes query:

In [290]:
def trader_joes_query(zip, coord_dict, zipradius):
    trader_joes= []

    params = { 
            "query": f"trader+joes+in+{zip}",
            "location": coord_dict,
            "address": f"zipcode {zip}",
            "radius": zipradius,
            "region": "us",
            "type": "grocery_or_supermarket,supermarket",
            "key": config.api_key,
            }

    endpoint_url= "https://maps.googleapis.com/maps/api/place/textsearch/json"

    res = requests.get(endpoint_url, params = params)
    results = res.json()
    trader_joes.extend(results['results'])
    time.sleep(2)
    while "next_page_token" in results:
        params['pagetoken'] = results['next_page_token'],
        res = requests.get(endpoint_url, params = params)
        results = json.loads(res.content)
        trader_joes.extend(results['results'])
        time.sleep(2)

    shop_name = []
    formatted_address = []
    shop_lat = []
    shop_lng = []
    type = []

    for i in range(len(trader_joes)):
        shop = trader_joes[i]

        try:
            shop_name.append(shop['name'])
        except:
            shop_name.append('none')

        try:
            formatted_address.append(shop['formatted_address'])
        except:
            formatted_address.append('none')

        try:
            shop_lat.append(shop['geometry']['location']['lat'])
        except:
            shop_lat.append('none')

        try:
            shop_lng.append(shop['geometry']['location']['lng'])
        except:
            shop_lng.append('none')
        
        try:
            type.append(shop['types'])
        except:
            type.append('none')

    df_dict = {'shop_name':shop_name, 'shop_address':formatted_address, 'shop_lat':shop_lat, 'shop_lng':shop_lng, 'types':type}

    trader_joes = pd.DataFrame(df_dict)

    #trader_joes.to_csv(f'Data/API_queries/grocery/trader_joes/trader_joes{zip}.csv')

    return trader_joes


Target query:

In [291]:
def target_query(zip, coord_dict, zipradius):
    target= []

    params = { 
            "query": f"target+in+{zip}",
            "location": coord_dict,
            "address": f"zipcode {zip}",
            "radius": zipradius,
            "region": "us",
            "type": "grocery_or_supermarket,supermarket",
            "key": config.api_key,
            }

    endpoint_url= "https://maps.googleapis.com/maps/api/place/textsearch/json"

    res = requests.get(endpoint_url, params = params)
    results = res.json()
    target.extend(results['results'])
    time.sleep(2)
    while "next_page_token" in results:
        params['pagetoken'] = results['next_page_token'],
        res = requests.get(endpoint_url, params = params)
        results = json.loads(res.content)
        target.extend(results['results'])
        time.sleep(2)

    shop_name = []
    formatted_address = []
    shop_lat = []
    shop_lng = []
    type = []

    for i in range(len(target)):
        shop = target[i]

        try:
            shop_name.append(shop['name'])
        except:
            shop_name.append('none')

        try:
            formatted_address.append(shop['formatted_address'])
        except:
            formatted_address.append('none')

        try:
            shop_lat.append(shop['geometry']['location']['lat'])
        except:
            shop_lat.append('none')

        try:
            shop_lng.append(shop['geometry']['location']['lng'])
        except:
            shop_lng.append('none')
        
        try:
            type.append(shop['types'])
        except:
            type.append('none')

    df_dict = {'shop_name':shop_name, 'shop_address':formatted_address, 'shop_lat':shop_lat, 'shop_lng':shop_lng, 'types':type}

    target = pd.DataFrame(df_dict)

    #target.to_csv(f'Data/API_queries/grocery/target/target{zip}.csv')

    return target


Food Lion query:

In [292]:
def food_lion_query(zip, coord_dict, zipradius):
    food_lion= []

    params = { 
            "query": f"food+lion+in+{zip}",
            "location": coord_dict,
            "address": f"zipcode {zip}",
            "radius": zipradius,
            "region": "us",
            "type": "grocery_or_supermarket,supermarket",
            "key": config.api_key,
            }

    endpoint_url= "https://maps.googleapis.com/maps/api/place/textsearch/json"

    res = requests.get(endpoint_url, params = params)
    results = res.json()
    food_lion.extend(results['results'])
    time.sleep(2)
    while "next_page_token" in results:
        params['pagetoken'] = results['next_page_token'],
        res = requests.get(endpoint_url, params = params)
        results = json.loads(res.content)
        food_lion.extend(results['results'])
        time.sleep(2)

    shop_name = []
    formatted_address = []
    shop_lat = []
    shop_lng = []
    type = []

    for i in range(len(food_lion)):
        shop = food_lion[i]

        try:
            shop_name.append(shop['name'])
        except:
            shop_name.append('none')

        try:
            formatted_address.append(shop['formatted_address'])
        except:
            formatted_address.append('none')

        try:
            shop_lat.append(shop['geometry']['location']['lat'])
        except:
            shop_lat.append('none')

        try:
            shop_lng.append(shop['geometry']['location']['lng'])
        except:
            shop_lng.append('none')
        
        try:
            type.append(shop['types'])
        except:
            type.append('none')

    df_dict = {'shop_name':shop_name, 'shop_address':formatted_address, 'shop_lat':shop_lat, 'shop_lng':shop_lng, 'types':type}

    food_lion = pd.DataFrame(df_dict)

   # food_lion.to_csv(f'Data/API_queries/grocery/food_lion/food_lion{zip}.csv')

    return food_lion

save a lot query:

In [293]:
def save_a_lot_query(zip, coord_dict, zipradius):
    save_a_lot= []

    params = { 
            "query": f"save+a+lot+in+{zip}",
            "location": coord_dict,
            "address": f"zipcode {zip}",
            "radius": zipradius,
            "region": "us",
            "type": "grocery_or_supermarket,supermarket",
            "key": config.api_key,
            }

    endpoint_url= "https://maps.googleapis.com/maps/api/place/textsearch/json"

    res = requests.get(endpoint_url, params = params)
    results = res.json()
    save_a_lot.extend(results['results'])
    time.sleep(2)
    while "next_page_token" in results:
        params['pagetoken'] = results['next_page_token'],
        res = requests.get(endpoint_url, params = params)
        results = json.loads(res.content)
        save_a_lot.extend(results['results'])
        time.sleep(2)

    shop_name = []
    formatted_address = []
    shop_lat = []
    shop_lng = []
    type = []

    for i in range(len(save_a_lot)):
        shop = save_a_lot[i]

        try:
            shop_name.append(shop['name'])
        except:
            shop_name.append('none')

        try:
            formatted_address.append(shop['formatted_address'])
        except:
            formatted_address.append('none')

        try:
            shop_lat.append(shop['geometry']['location']['lat'])
        except:
            shop_lat.append('none')

        try:
            shop_lng.append(shop['geometry']['location']['lng'])
        except:
            shop_lng.append('none')
        
        try:
            type.append(shop['types'])
        except:
            type.append('none')

    df_dict = {'shop_name':shop_name, 'shop_address':formatted_address, 'shop_lat':shop_lat, 'shop_lng':shop_lng, 'types':type}

    save_a_lot = pd.DataFrame(df_dict)

   # save_a_lot.to_csv(f'Data/API_queries/grocery/save_a_lot/save_a_lot{zip}.csv')

    return save_a_lot

HG Hills query:

In [294]:
def HG_Hill_query(zip, coord_dict, zipradius):
    HG_Hill= []

    params = { 
            "query": f"HG+Hill+in+{zip}",
            "location": coord_dict,
            "address": f"zipcode {zip}",
            "radius": zipradius,
            "region": "us",
            "type": "grocery_or_supermarket,supermarket",
            "key": config.api_key,
            }

    endpoint_url= "https://maps.googleapis.com/maps/api/place/textsearch/json"

    res = requests.get(endpoint_url, params = params)
    results = res.json()
    HG_Hill.extend(results['results'])
    time.sleep(2)
    while "next_page_token" in results:
        params['pagetoken'] = results['next_page_token'],
        res = requests.get(endpoint_url, params = params)
        results = json.loads(res.content)
        HG_Hill.extend(results['results'])
        time.sleep(2)

    shop_name = []
    formatted_address = []
    shop_lat = []
    shop_lng = []
    type = []

    for i in range(len(HG_Hill)):
        shop = HG_Hill[i]

        try:
            shop_name.append(shop['name'])
        except:
            shop_name.append('none')

        try:
            formatted_address.append(shop['formatted_address'])
        except:
            formatted_address.append('none')

        try:
            shop_lat.append(shop['geometry']['location']['lat'])
        except:
            shop_lat.append('none')

        try:
            shop_lng.append(shop['geometry']['location']['lng'])
        except:
            shop_lng.append('none')
        
        try:
            type.append(shop['types'])
        except:
            type.append('none')

    df_dict = {'shop_name':shop_name, 'shop_address':formatted_address, 'shop_lat':shop_lat, 'shop_lng':shop_lng, 'types':type}

    HG_Hill = pd.DataFrame(df_dict)

    #HG_Hill.to_csv(f'Data/API_queries/grocery/HG_Hill/HG_Hill{zip}.csv')

    return HG_Hill

Bi-Rite query:

In [295]:
def bi_rite_query(zip, coord_dict, zipradius):
    bi_rite= []

    params = { 
            "query": f"Bi-Rite+in+{zip}",
            "location": coord_dict,
            "address": f"zipcode {zip}",
            "radius": zipradius,
            "region": "us",
            "type": "grocery_or_supermarket,supermarket",
            "key": config.api_key,
            }

    endpoint_url= "https://maps.googleapis.com/maps/api/place/textsearch/json"

    res = requests.get(endpoint_url, params = params)
    results = res.json()
    bi_rite.extend(results['results'])
    time.sleep(2)
    while "next_page_token" in results:
        params['pagetoken'] = results['next_page_token'],
        res = requests.get(endpoint_url, params = params)
        results = json.loads(res.content)
        bi_rite.extend(results['results'])
        time.sleep(2)

    shop_name = []
    formatted_address = []
    shop_lat = []
    shop_lng = []
    type = []

    for i in range(len(bi_rite)):
        shop = bi_rite[i]

        try:
            shop_name.append(shop['name'])
        except:
            shop_name.append('none')

        try:
            formatted_address.append(shop['formatted_address'])
        except:
            formatted_address.append('none')

        try:
            shop_lat.append(shop['geometry']['location']['lat'])
        except:
            shop_lat.append('none')

        try:
            shop_lng.append(shop['geometry']['location']['lng'])
        except:
            shop_lng.append('none')
        
        try:
            type.append(shop['types'])
        except:
            type.append('none')

    df_dict = {'shop_name':shop_name, 'shop_address':formatted_address, 'shop_lat':shop_lat, 'shop_lng':shop_lng, 'types':type}

    bi_rite = pd.DataFrame(df_dict)

   # bi_rite.to_csv(f'Data/API_queries/grocery/bi_rite/bi_rite{zip}.csv')

    return bi_rite

# queries by zipcode

for-loop that will iterate through all zip codes and run all query functions

In [299]:
for zip_code in zip_codes:
    coord = zip_codes[zip_code]["coord"]
    radius = zip_codes[zip_code]["radius"]
    zip_codes[zip_code]["dataframe"] = { "grocery": grocery_query(zip_code, coord, radius),
                                         "gas_station": gasstation_query(zip_code, coord, radius),
                                         "convenience_store": convstore_query(zip_code, coord, radius),
                                         "restaurant": restaurant_query(zip_code, coord, radius),
                                         "truegrocery": truegrocery_query(zip_code, coord, radius),
                                         "kroger": kroger_query(zip_code, coord, radius),
                                         "publix": publix_query(zip_code, coord, radius),
                                         "walmart": walmart_query(zip_code, coord, radius),
                                         "ALDI": ALDI_query(zip_code, coord, radius),
                                         "piggly_wiggly": piggly_wiggly_query(zip_code, coord, radius),
                                         "turnip_truck": turnip_truck_query(zip_code, coord, radius),
                                         "whole_foods": whole_foods_query(zip_code, coord, radius),
                                         "trader_joes": trader_joes_query(zip_code, coord, radius),
                                         "target": target_query(zip_code, coord, radius),
                                         "food_lion": food_lion_query(zip_code, coord, radius),
                                         "save_a_lot": save_a_lot_query(zip_code, coord, radius),
                                         "HG_Hill": HG_Hill_query(zip_code, coord, radius),
                                         "bi_rite": bi_rite_query(zip_code, coord, radius),}

code to create master DataFrame:


In [ ]:
# DFs = []
# for zip_code in zip_codes:
#      for key in zip_codes[zip_code]['dataframe']:
#         DFs.append(zip_codes[zip_code]['dataframe'][key])

# allqueries_df = pd.concat(DFs, ignore_index=True)

In [ ]:
allqueries_df

In [ ]:
#allqueries_df.to_csv(f'Data/API_queries/allqueries_df.csv')

In [277]:
zip_codes[37203]["dataframe"].keys()

dict_keys(['bi_rite'])

individual groceries:

In [300]:
# kroger_df = []
# for zip_code in zip_codes:
#      kroger_df.append(zip_codes[zip_code]["dataframe"]["kroger"])

# kroger_df = pd.concat(kroger_df, ignore_index=True)

In [302]:
# kroger_df.to_csv(f'Data/API_queries/kroger_df.csv')

In [303]:
# publix_df = []
# for zip_code in zip_codes:
#      publix_df.append(zip_codes[zip_code]["dataframe"]["publix"])

# publix_df = pd.concat(publix_df, ignore_index=True)

# publix_df.to_csv(f'Data/API_queries/publix_df.csv')

In [304]:
# walmart_df = []
# for zip_code in zip_codes:
#      walmart_df.append(zip_codes[zip_code]["dataframe"]["walmart"])

# walmart_df = pd.concat(walmart_df, ignore_index=True)

# walmart_df.to_csv(f'Data/API_queries/walmart_df.csv')

In [305]:
# ALDI_df = []
# for zip_code in zip_codes:
#      ALDI_df.append(zip_codes[zip_code]["dataframe"]["ALDI"])

# ALDI_df = pd.concat(ALDI_df, ignore_index=True)

# ALDI_df.to_csv(f'Data/API_queries/ALDI_df.csv')

In [306]:
# piggly_wiggly_df = []
# for zip_code in zip_codes:
#      piggly_wiggly_df.append(zip_codes[zip_code]["dataframe"]["piggly_wiggly"])

# piggly_wiggly_df = pd.concat(piggly_wiggly_df, ignore_index=True)

# piggly_wiggly_df.to_csv(f'Data/API_queries/piggly_wiggly_df.csv')

In [307]:
# turnip_truck_df = []
# for zip_code in zip_codes:
#      turnip_truck_df.append(zip_codes[zip_code]["dataframe"]["turnip_truck"])

# turnip_truck_df = pd.concat(turnip_truck_df, ignore_index=True)

# turnip_truck_df.to_csv(f'Data/API_queries/turnip_truck_df.csv')

In [308]:
# whole_foods_df = []
# for zip_code in zip_codes:
#      whole_foods_df.append(zip_codes[zip_code]["dataframe"]["whole_foods"])

# whole_foods_df = pd.concat(whole_foods_df, ignore_index=True)

# whole_foods_df.to_csv(f'Data/API_queries/whole_foods_df.csv')

In [309]:
# trader_joes_df = []
# for zip_code in zip_codes:
#      trader_joes_df.append(zip_codes[zip_code]["dataframe"]["trader_joes"])

# trader_joes_df = pd.concat(trader_joes_df, ignore_index=True)

# trader_joes_df.to_csv(f'Data/API_queries/trader_joes_df.csv')

In [310]:
# target_df = []
# for zip_code in zip_codes:
#      target_df.append(zip_codes[zip_code]["dataframe"]["target"])

# target_df = pd.concat(target_df, ignore_index=True)

# target_df.to_csv(f'Data/API_queries/target_df.csv')

In [311]:
# food_lion_df = []
# for zip_code in zip_codes:
#      food_lion_df.append(zip_codes[zip_code]["dataframe"]["food_lion"])

# food_lion_df = pd.concat(food_lion_df, ignore_index=True)

# food_lion_df.to_csv(f'Data/API_queries/food_lion_df.csv')

In [312]:
# save_a_lot_df = []
# for zip_code in zip_codes:
#      save_a_lot_df.append(zip_codes[zip_code]["dataframe"]["save_a_lot"])

# save_a_lot_df = pd.concat(save_a_lot_df, ignore_index=True)

# save_a_lot_df.to_csv(f'Data/API_queries/save_a_lot_df.csv')

In [313]:
# HG_Hill_df = []
# for zip_code in zip_codes:
#      HG_Hill_df.append(zip_codes[zip_code]["dataframe"]["HG_Hill"])

# HG_Hill_df = pd.concat(HG_Hill_df, ignore_index=True)

# HG_Hill_df.to_csv(f'Data/API_queries/HG_Hill_df.csv')

In [314]:
# bi_rite_df = []
# for zip_code in zip_codes:
#      bi_rite_df.append(zip_codes[zip_code]["dataframe"]["bi_rite"])

# bi_rite_df = pd.concat(bi_rite_df, ignore_index=True)

# bi_rite_df.to_csv(f'Data/API_queries/bi_rite_df.csv')

code to create master grocery DataFrame:

In [ ]:
# groceries_df = []
# for zip_code in zip_codes:
#      groceries_df.append(zip_codes[zip_code]['dataframe']['grocery'])

# groceries_df = pd.concat(groceries_df, ignore_index=True)

In [ ]:
groceries_df

In [ ]:
#groceries_df.to_csv(f'Data/API_queries/groceries_df.csv')

code to create master gas_station DF

In [ ]:
# gasstations_df = []
# for zip_code in zip_codes:
#      gasstations_df.append(zip_codes[zip_code]['dataframe']['gas_station'])

# gasstations_df = pd.concat(gasstations_df, ignore_index=True)

In [ ]:
# gasstations_df

In [ ]:
#gasstations_df.to_csv(f'Data/API_queries/gasstations_df.csv')

code to create master convenience_store DF

In [ ]:
# conveniencestore_df = []
# for zip_code in zip_codes:
#      conveniencestore_df.append(zip_codes[zip_code]['dataframe']['convenience_store'])

# conveniencestore_df = pd.concat(conveniencestore_df, ignore_index=True)

In [ ]:
# conveniencestore_df

In [ ]:
#conveniencestore_df.to_csv(f'Data/API_queries/conveniencestore_df.csv')

code to create master restaurant DF

In [ ]:
# restaurant_df = []
# for zip_code in zip_codes:
#      restaurant_df.append(zip_codes[zip_code]['dataframe']['restaurant'])

# restaurant_df = pd.concat(restaurant_df, ignore_index=True)

In [ ]:
# restaurant_df

In [ ]:
#restaurant_df.to_csv(f'Data/API_queries/restaurant_df.csv')

In [224]:
# truegrocery_df = []
# for zip_code in zip_codes:
#      truegrocery_df.append(zip_codes[zip_code]['dataframe']['truegrocery'])

# truegrocery_df = pd.concat(truegrocery_df, ignore_index=True)

In [227]:
# truegrocery_df

shop_name  \
0                                         Kroger   
1                                         Kroger   
2           Publix Super Market at The Crossings   
3    Publix Super Market at Mt. View Marketplace   
4                                         Kroger   
5   Publix Super Market at Hill Center Greenwood   
6                                         Kroger   
7                                           ALDI   
8                                         Kroger   
9                                      Food Lion   
10         Publix Super Market at Nippers Corner   
11                                        Kroger   
12                           Walmart Supercenter   
13                                        Kroger   
14                                        Kroger   
15                           Walmart Supercenter   
16                                        Kroger   
17             The Turnip Truck - East Nashville   
18                                        Kroger   
19                                     Food Lion   

                                   shop_address   shop_lat   shop_lng  \
0   2284 Murfreesboro Pike, Nashville, TN 37217  36.088656 -86.647154   
1         61 E Thompson Ln, Nashville, TN 37211  36.109818 -86.725069   
2        2324 Lebanon Pike, Nashville, TN 37214  36.170783 -86.683999   
3     3532 Murfreesboro Pike, Antioch, TN 37013  36.053391 -86.614928   
4            5319 Mt View Rd, Antioch, TN 37013  36.049621 -86.647099   
5        1111 Gallatin Ave, Nashville, TN 37206  36.189846 -86.744947   
6          143 McGavock Pk, Nashville, TN 37214  36.170859 -86.678731   
7           1911 Ransom Pl, Nashville, TN 37217  36.088124 -86.650808   
8         711 Gallatin Ave, Nashville, TN 37206  36.184430 -86.746857   
9             3636 Bell Rd, Nashville, TN 37214  36.150496 -86.627243   
10  15544 Old Hickory Blvd, Nashville, TN 37211  36.041027 -86.741441   
11   5771 Nolensville Road, Nashville, TN 37211  36.046395 -86.715243   
12   3035 Hamilton Church Rd, Antioch, TN 37013  36.060974 -86.629125   
13      3410 Gallatin Pike, Nashville, TN 37216  36.210136 -86.731665   
14     5713 Edmondson Pike, Nashville, TN 37211  36.039181 -86.745405   
15   4040 Nolensville Pike, Nashville, TN 37211  36.082472 -86.725605   
16      2615 Franklin Pike, Nashville, TN 37204  36.119945 -86.777180   
17         701 Woodland St, Nashville, TN 37206  36.173825 -86.760016   
18           800 Monroe St, Nashville, TN 37208  36.175880 -86.794248   
19           936 Richards Rd, Antioch, TN 37013  36.068003 -86.681300   

                                                types  
0   [grocery_or_supermarket, food, point_of_intere...  
1   [grocery_or_supermarket, food, point_of_intere...  
2   [supermarket, florist, bakery, grocery_or_supe...  
3   [supermarket, florist, bakery, grocery_or_supe...  
4   [grocery_or_supermarket, food, point_of_intere...  
5   [supermarket, florist, bakery, grocery_or_supe...  
6   [grocery_or_supermarket, food, point_of_intere...  
7   [supermarket, grocery_or_supermarket, food, po...  
8   [grocery_or_supermarket, food, point_of_intere...  
9   [grocery_or_supermarket, food, point_of_intere...  
10  [supermarket, florist, bakery, grocery_or_supe...  
11  [grocery_or_supermarket, food, point_of_intere...  
12  [department_store, hardware_store, bakery, gro...  
13  [grocery_or_supermarket, food, point_of_intere...  
14  [grocery_or_supermarket, food, point_of_intere...  
15  [department_store, hardware_store, bakery, gro...  
16  [grocery_or_supermarket, food, point_of_intere...  
17  [grocery_or_supermarket, food, health, point_o...  
18  [grocery_or_supermarket, food, point_of_intere...  
19  [grocery_or_supermarket, food, point_of_intere...

# importing grocery_chains_df.csv and then beginning to create MVP folium map

In [39]:
grocery_chains_df = pd.read_csv('Data/grocery_chains_df.csv').drop(columns= 'Unnamed: 0')

In [42]:
grocery_chains_df.head(2)

shop_name                             shop_address   shop_lat   shop_lng  \
0      ALDI    615 Gallatin Ave, Nashville, TN 37206  36.183288 -86.747552   
1      ALDI  135 S. Gallatin Pike, Madison, TN 37115  36.261670 -86.711514   

                                               types  zip_code  
0  ['supermarket', 'grocery_or_supermarket', 'foo...     37206  
1  ['supermarket', 'grocery_or_supermarket', 'foo...     37115

In [192]:
for i in range(0,len(grocery_chains_df)):
   folium.Circle(
      location=[grocery_chains_df.iloc[i]['shop_lat'], grocery_chains_df.iloc[i]['shop_lng']],
      popup=grocery_chains_df.iloc[i]['shop_name'],
      radius=1609,
      color='green',
      fill=True,
      fill_color='lightgreen'
   ).add_to(nash_map)

In [43]:
# for row_index, row_values in grocery_chains_df.iterrows() :
#     loc = [row_values['shop_lat'], row_values['shop_lng']]
#     pop = str(row_values['shop_name'])
#     icon = folium.Icon(color = 'beige', icon = 'beer', prefix = 'fa')

#     marker = folium.Marker(
#             location = loc,
#             popup = pop, icon = icon)

#     marker.add_to(nash_map)

In [193]:
nash_map

In [194]:
nash_map.save('Data/nash_map.html')

# scratch coding area

In [169]:
fixednashdisease2018 = pd.read_csv('/Users/k.simmons/Desktop/NSS/data analytics bootcamp/capstone/Data/CDC data/nashdisease2018.csv')

In [170]:
fixednashdisease2018['Geolocation'] = fixednashdisease2018['Geolocation'].str.replace('(','')
fixednashdisease2018['Geolocation'] = fixednashdisease2018['Geolocation'].str.replace(')','')
fixednashdisease2018['Geolocation'] = fixednashdisease2018['Geolocation'].str.replace('POINT ','')

/var/folders/s3/87cx_4f97x52rgnl47c9skpr0000gn/T/ipykernel_69616/1525793894.py:1: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.
  fixednashdisease2018['Geolocation'] = fixednashdisease2018['Geolocation'].str.replace('(','')
/var/folders/s3/87cx_4f97x52rgnl47c9skpr0000gn/T/ipykernel_69616/1525793894.py:2: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.
  fixednashdisease2018['Geolocation'] = fixednashdisease2018['Geolocation'].str.replace(')','')


In [171]:
fixednashdisease2018['Geolocation'][1]

'-86.8675409005 36.3479505187'

In [172]:
newcoords_df = fixednashdisease2018['Geolocation'].str.split(pat=None, n=0, expand=True, regex=False)

In [153]:
fixednashdisease2018.head(1)

Unnamed: 0 StateAbbr  PlaceName  PlaceFIPS    TractFIPS  \
0         106        TN  Nashville    4752006  47037018405   

         Place_TractID  Population2010  ACCESS2_CrudePrev ACCESS2_Crude95CI  \
0  4752006-47037018405            4760                7.6      ( 6.1,  9.4)   

   ARTHRITIS_CrudePrev  ... PHLTH_Crude95CI  SLEEP_CrudePrev SLEEP_Crude95CI  \
0                 25.3  ...    ( 8.7, 11.4)             34.7    (32.9, 36.6)   

   STROKE_CrudePrev STROKE_Crude95CI  TEETHLOST_CrudePrev TEETHLOST_Crude95CI  \
0               2.1     ( 1.8,  2.4)                  7.3        ( 4.3, 11.3)   

                    Geolocation new_x  new_y  
0  -86.9407121165 36.0521853395               

[1 rows x 66 columns]

In [148]:
newcoords_df

0              1
0    -86.9407121165  36.0521853395
1    -86.8675409005  36.3479505187
2    -86.8538782901  36.2488660642
3    -86.7140695527   36.069945042
4    -86.6732926633   36.073922218
..              ...            ...
151  -86.7820995582   36.120319646
152  -86.7940986863  36.1125202586
153  -86.6797916232   36.049231748
154  -86.7293550121  36.2111454796
155  -86.7590618024  36.1790862802

[156 rows x 2 columns]

In [164]:
xcoord = newcoords_df[1].tolist()
ycoord = newcoords_df[0].tolist()

In [173]:
fixednashdisease2018['new_x'] = xcoord
fixednashdisease2018['new_y'] = ycoord

In [175]:
fixednashdisease2018['fixed_geo'] = fixednashdisease2018['new_x'] + ', ' + fixednashdisease2018['new_y']

In [178]:
fixednashdisease2018['fixed_geo']

0      36.0521853395, -86.9407121165
1      36.3479505187, -86.8675409005
2      36.2488660642, -86.8538782901
3       36.069945042, -86.7140695527
4       36.073922218, -86.6732926633
                   ...              
151     36.120319646, -86.7820995582
152    36.1125202586, -86.7940986863
153     36.049231748, -86.6797916232
154    36.2111454796, -86.7293550121
155    36.1790862802, -86.7590618024
Name: fixed_geo, Length: 156, dtype: object

In [186]:
fixednashdisease2018 = fixednashdisease2018.drop(columns= 'Unnamed: 0')

In [187]:
#fixednashdisease2018.to_excel('Data/fixednashdisease2018.xlsx')

In [167]:
for row in fixednashdisease2018.iterrows():

    fixednashdisease2018['new_x'].append(xcoord)
   # fixednashdisease2018['new_y'].append(ycoord)

#return fixednashdisease2018



/var/folders/s3/87cx_4f97x52rgnl47c9skpr0000gn/T/ipykernel_69616/814770259.py:3: FutureWarning: The series.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fixednashdisease2018['new_x'].append(xcoord)


TypeError: cannot concatenate object of type '<class 'str'>'; only Series and DataFrame objs are valid

In [158]:
fixednashdisease2018

Unnamed: 0 StateAbbr  PlaceName  PlaceFIPS    TractFIPS  \
0           106        TN  Nashville    4752006  47037018405   
1           281        TN  Nashville    4752006  47037010103   
2           297        TN  Nashville    4752006  47037010105   
3           589        TN  Nashville    4752006  47037019004   
4           862        TN  Nashville    4752006  47037015615   
..          ...       ...        ...        ...          ...   
151       26862        TN  Nashville    4752006  47037017100   
152       27018        TN  Nashville    4752006  47037017800   
153       27034        TN  Nashville    4752006  47037019111   
154       27051        TN  Nashville    4752006  47037011200   
155       27207        TN  Nashville    4752006  47037011900   

           Place_TractID  Population2010  ACCESS2_CrudePrev ACCESS2_Crude95CI  \
0    4752006-47037018405            4760                7.6      ( 6.1,  9.4)   
1    4752006-47037010103            2377               11.1      ( 9.3, 13.3)   
2    4752006-47037010105            4268               13.5      (11.0, 16.0)   
3    4752006-47037019004            4407               29.9      (26.3, 33.2)   
4    4752006-47037015615            4775               25.7      (22.5, 28.8)   
..                   ...             ...                ...               ...   
151  4752006-47037017100            1659                8.9      ( 6.9, 11.8)   
152  4752006-47037017800            4858                7.6      ( 6.4,  9.4)   
153  4752006-47037019111            4163               17.4      (14.9, 20.3)   
154  4752006-47037011200            4133               13.4      (11.0, 16.1)   
155  4752006-47037011900            2429               19.5      (16.5, 23.0)   

     ARTHRITIS_CrudePrev  ... PHLTH_Crude95CI  SLEEP_CrudePrev  \
0                   25.3  ...    ( 8.7, 11.4)             34.7   
1                   32.6  ...    (12.8, 15.7)             36.2   
2                   32.0  ...    (12.4, 15.8)             43.1   
3                   25.6  ...    (17.1, 20.0)             43.8   
4                   24.0  ...    (15.0, 17.6)             43.7   
..                   ...  ...             ...              ...   
151                 18.8  ...    ( 7.0,  9.1)             35.8   
152                 20.0  ...    ( 7.5,  9.2)             33.3   
153                 19.4  ...    (10.6, 12.9)             41.7   
154                 25.8  ...    (11.6, 14.9)             39.3   
155                 24.3  ...    (13.1, 16.2)             44.9   

    SLEEP_Crude95CI  STROKE_CrudePrev STROKE_Crude95CI  TEETHLOST_CrudePrev  \
0      (32.9, 36.6)               2.1     ( 1.8,  2.4)                  7.3   
1      (34.8, 37.6)               3.3     ( 3.0,  3.7)                 13.2   
2      (41.4, 44.7)               4.3     ( 3.8,  4.9)                 15.1   
3      (42.6, 45.0)               4.0     ( 3.7,  4.3)                 30.3   
4      (42.4, 44.9)               3.3     ( 3.1,  3.6)                 23.2   
..              ...               ...              ...                  ...   
151    (34.0, 37.7)               2.0     ( 1.7,  2.2)                  8.9   
152    (32.0, 34.7)               1.8     ( 1.6,  1.9)                  7.2   
153    (40.2, 43.2)               2.1     ( 2.0,  2.4)                 15.2   
154    (37.5, 41.0)               2.9     ( 2.6,  3.2)                 14.6   
155    (43.2, 46.6)               3.8     ( 3.3,  4.2)                 23.1   

    TEETHLOST_Crude95CI                   Geolocation new_x  new_y  
0          ( 4.3, 11.3)  -86.9407121165 36.0521853395               
1          ( 9.3, 18.2)  -86.8675409005 36.3479505187               
2          (10.1, 21.1)  -86.8538782901 36.2488660642               
3          (22.1, 38.6)   -86.7140695527 36.069945042               
4          (16.7, 29.7)   -86.6732926633 36.073922218               
..                  ...                           ...   ...    ...  
151        ( 5.1, 14.2)   -86.78209955

In [145]:
fixednashdisease2018

Unnamed: 0 StateAbbr  PlaceName  PlaceFIPS    TractFIPS  \
0           106        TN  Nashville    4752006  47037018405   
1           281        TN  Nashville    4752006  47037010103   
2           297        TN  Nashville    4752006  47037010105   
3           589        TN  Nashville    4752006  47037019004   
4           862        TN  Nashville    4752006  47037015615   
..          ...       ...        ...        ...          ...   
151       26862        TN  Nashville    4752006  47037017100   
152       27018        TN  Nashville    4752006  47037017800   
153       27034        TN  Nashville    4752006  47037019111   
154       27051        TN  Nashville    4752006  47037011200   
155       27207        TN  Nashville    4752006  47037011900   

           Place_TractID  Population2010  ACCESS2_CrudePrev ACCESS2_Crude95CI  \
0    4752006-47037018405            4760                7.6      ( 6.1,  9.4)   
1    4752006-47037010103            2377               11.1      ( 9.3, 13.3)   
2    4752006-47037010105            4268               13.5      (11.0, 16.0)   
3    4752006-47037019004            4407               29.9      (26.3, 33.2)   
4    4752006-47037015615            4775               25.7      (22.5, 28.8)   
..                   ...             ...                ...               ...   
151  4752006-47037017100            1659                8.9      ( 6.9, 11.8)   
152  4752006-47037017800            4858                7.6      ( 6.4,  9.4)   
153  4752006-47037019111            4163               17.4      (14.9, 20.3)   
154  4752006-47037011200            4133               13.4      (11.0, 16.1)   
155  4752006-47037011900            2429               19.5      (16.5, 23.0)   

     ARTHRITIS_CrudePrev  ... PAPTEST_Crude95CI  PHLTH_CrudePrev  \
0                   25.3  ...      (83.5, 88.0)             10.0   
1                   32.6  ...      (80.9, 85.4)             14.3   
2                   32.0  ...      (84.3, 88.3)             13.9   
3                   25.6  ...      (79.5, 83.2)             18.5   
4                   24.0  ...      (81.6, 85.1)             16.3   
..                   ...  ...               ...              ...   
151                 18.8  ...      (83.7, 89.0)              7.9   
152                 20.0  ...      (83.7, 87.5)              8.3   
153                 19.4  ...      (82.5, 86.3)             11.8   
154                 25.8  ...      (82.9, 87.5)             13.1   
155                 24.3  ...      (83.2, 87.6)             14.6   

    PHLTH_Crude95CI  SLEEP_CrudePrev SLEEP_Crude95CI  STROKE_CrudePrev  \
0      ( 8.7, 11.4)             34.7    (32.9, 36.6)               2.1   
1      (12.8, 15.7)             36.2    (34.8, 37.6)               3.3   
2      (12.4, 15.8)             43.1    (41.4, 44.7)               4.3   
3      (17.1, 20.0)             43.8    (42.6, 45.0)               4.0   
4      (15.0, 17.6)             43.7    (42.4, 44.9)               3.3   
..              ...              ...             ...               ...   
151    ( 7.0,  9.1)             35.8    (34.0, 37.7)               2.0   
152    ( 7.5,  9.2)             33.3    (32.0, 34.7)               1.8   
153    (10.6, 12.9)             41.7    (40.2, 43.2)               2.1   
154    (11.6, 14.9)             39.3    (37.5, 41.0)               2.9   
155    (13.1, 16.2)             44.9    (43.2, 46.6)               3.8   

    STROKE_Crude95CI  TEETHLOST_CrudePrev TEETHLOST_Crude95CI  \
0       ( 1.8,  2.4)                  7.3        ( 4.3, 11.3)   
1       ( 3.0,  3.7)                 13.2        ( 9.3, 18.2)   
2       ( 3.8,  4.9)                 15.1        (10.1, 21.1)   
3       ( 3.7,  4.3)                 30.3        (22.1, 38.6)   
4       ( 3.1,  3.6)                 23.2        (16.7, 29.7)   
..               ...                  ...                 ...   
151     ( 1.7,  2.2)                  8.9        ( 5.1, 14.2)   
152     ( 1.6,  1.9)                 

In [ ]:
#zip_code = 37216
#coord = zip_codes[zip_code]["coord"]
#radius = zip_codes[zip_code]["radius"]
##zip_codes[zip_code]["dataframe"] = { "grocery": grocery_query(zip_code, coord, radius),
                                    # "gas_station": gasstation_query(zip_code, coord, radius),
                                   #  "convenience_store": convstore_query(zip_code, coord, radius),
                                   #  "restaurant": restaurant_query(zip_code, coord, radius),}

In [ ]:
#zip_code = 37216
#coord = zip_codes[zip_code]["coord"]
#radius = zip_codes[zip_code]["radius"]
#zip_codes[zip_code]["dataframe"] = {"junkfood": junkfood_query(zip_code, coord, radius),}

In [ ]:
#junkfood_query(37216, coord_dict['coord37216'], zipradius['radius37216'])

# following code is trial and error test coding

following is test query performed on one zipcode, while troubleshooting query results

In [ ]:
#gmaps = googlemaps.Client(key={api_key})

In [ ]:
#not needed i guess ?????????????

#url = "https://maps.googleapis.com/maps/api/place/textsearch/json?query=grocery%20stores%20in%20Nashville%20Tennessee&key={api_key}"

#payload={}
#headers = {}

#response = requests.request('GET', url, headers=headers, data=payload)

In [ ]:
#place types used: grocery_or_supermarket, supermarket, bakery, food

#grocery_stores37216 = []
#params37216 = {}

#endpoint_url37216 = "https://maps.googleapis.com/maps/api/place/textsearch/json?query=grocery+store+in+37216&location=37216&region=us&type=grocery_or_supermarket,supermarket,bakery,food&key={api_key}"

#res37216 = requests.get(endpoint_url37216, params = params37216)
#results37216 = json.loads(res37216.content)
#grocery_stores37216.extend(results37216['results'])
#time.sleep(2)
#while "next_page_token" in results37216:#
   # params37216['pagetoken'] = results37216['next_page_token'],
   # res37216 = requests.get(endpoint_url37216, params = params37216)
    #results37216 = json.loads(res37216.content)
    #grocery_stores37216.extend(results37216['results'])
    #time.sleep(2)

In [ ]:
#res37216

In [ ]:
#results37216

In [ ]:
#shop_name37216 = []
#formatted_address37216 = []
#shop_lat37216 = []
#shop_lng37216 = []

#for i in range(len(grocery_stores37216)):
  #  shop37216 = grocery_stores37216[i]

  #  try:
  #      shop_name37216.append(shop37216['name'])
 #   except:
  #      shop_name37216.append('none')

  #  try:
  #      formatted_address37216.append(shop37216['formatted_address'])
  #  except:
  #      formatted_address37216.append('none')

 #   try:
 #       shop_lat37216.append(shop37216['geometry']['location']['lat'])
#    except:
  #      shop_lat37216.append('none')

  #  try:
 #       shop_lng37216.append(shop37216['geometry']['location']['lng'])
 #   except:
  #      shop_lng37216.append('none')

In [ ]:
#df_dict37216 = {'shop_name':shop_name37216, 'shop_address':formatted_address37216, 'shop_lat':shop_lat37216, 'shop_lng':shop_lng37216}

# grocery_stores37216_df = pd.DataFrame(df_dict37216)

#grocery_stores37216_df['duplicator'] = grocery_stores37216_df['shop_name'] + grocery_stores37216_df['shop_address']

#grocery_stores37216_df.drop_duplicates(['duplicator'], inplace=True)



In [ ]:
# grocery_stores37216_df

In [ ]:
# mixedresultsgrocery_stores37216_df = grocery_stores37216_df

In [ ]:
# results37216

In [ ]:
# mixedresultsgrocery_stores37216_df

In [ ]:
# #original test API query

# grocery_stores = []
# params1 = {}

# #endpoint_url1 = "https://maps.googleapis.com/maps/api/place/textsearch/json?query=grocery%20stores%20in%20Nashville%20Tennessee&key={api_key}"
         
# res1 = requests.get(endpoint_url1, params = params1)
# results1 =  json.loads(res1.content)
# grocery_stores.extend(results1['results'])
# time.sleep(2)
# while "next_page_token" in results1:
#      params1['pagetoken'] = results1['next_page_token'],
#      res1 = requests.get(endpoint_url1, params = params1)
#      results1 = json.loads(res1.content)
#      grocery_stores.extend(results1['results'])
#      time.sleep(2)

In [ ]:
# #original test API query


# shop_name1 = []
# formatted_address1 = []
# shop_lat1 = []
# shop_lng1 = []

# for i in range(len(grocery_stores)):
#     shop = grocery_stores[i]

#     try:
#         shop_name1.append(shop['name'])
#     except:
#         shop_name1.append('none')

#     try:
#         formatted_address1.append(shop['formatted_address'])
#     except:
#         formatted_address1.append('none')

#     try:
#         shop_lat1.append(shop['geometry']['location']['lat'])
#     except:
#         shop_lat1.append('none')

#     try:
#         shop_lng1.append(shop['geometry']['location']['lng'])
#     except:
#         shop_lng1.append('none')

In [ ]:
# #original test API query


# df_dict1 = {'shop_name':shop_name1, 'shop_address':formatted_address1, 'shop_lat':shop_lat1, 'shop_lng':shop_lng1}

# grocery_stores_df = pd.DataFrame(df_dict1)
# #grocery_stores_df['data_zipcode'] = data_zipcode
# grocery_stores_df['duplicator'] = grocery_stores_df['shop_name'] + grocery_stores_df['shop_address']

# grocery_stores_df.drop_duplicates(['duplicator'], inplace=True)

# #all_grocery_stores = all_grocery_stores.append(grocery_stores_df)

In [ ]:
#restaurants = []
#params2 = {}

#endpoint_url2 = "https://maps.googleapis.com/maps/api/place/textsearch/json?query=fast%20food%20in%20Nashville%20Tennessee&key={api_key}"
         
#res2 = requests.get(endpoint_url2, params = params2)
#results2 =  json.loads(res2.content)
#restaurants.extend(results2['results'])
#time.sleep(2)
#while "next_page_token" in results2:
     #params2['pagetoken'] = results2['next_page_token'],
     #res2 = requests.get(endpoint_url2, params = params2)
     #results2 = json.loads(res2.content)
     #restaurants.extend(results2['results'])
     #time.sleep(2)

In [ ]:
# #original test API query


# restaurants = []
# params2 = {}

# #endpoint_url2 = 'https://maps.googleapis.com/maps/api/place/textsearch/json?query=nashville+tn&type=restaurant&key={api_key}'
         
# res2 = requests.get(endpoint_url2, params = params2)
# results2 =  json.loads(res2.content)
# restaurants.extend(results2['results'])
# time.sleep(2)
# while "next_page_token" in results2:
#      params2['pagetoken'] = results2['next_page_token'],
#      res2 = requests.get(endpoint_url2, params = params2)
#      results2 = json.loads(res2.content)
#      restaurants.extend(results2['results'])
#      time.sleep(2)

In [ ]:
# #original test API query


# shop_name2 = []
# formatted_address2 = []
# shop_lat2 = []
# shop_lng2 = []

# for i in range(len(restaurants)):
#     shop2 = restaurants[i]

#     try:
#         # shop_name2.append(shop2['name'])
#     except:
#         shop_name2.append('none')

#     try:
#         formatted_address2.append(shop2['formatted_address'])
#     except:
#         formatted_address2.append('none')

#     try:
#         shop_lat2.append(shop2['geometry']['location']['lat'])
#     except:
#         shop_lat2.append('none')

#     try:
#         shop_lng2.append(shop2['geometry']['location']['lng'])
#     except:
#         shop_lng2.append('none')

In [ ]:
# #original test API query


# df_dict2 = {'shop_name':shop_name2, 'shop_address':formatted_address2, 'shop_lat':shop_lat2, 'shop_lng':shop_lng2}

# restaurants_df = pd.DataFrame(df_dict2)
# #grocery_stores_df['data_zipcode'] = data_zipcode
# restaurants_df['duplicator'] = restaurants_df['shop_name'] + restaurants_df['shop_address']

# restaurants_df.drop_duplicates(['duplicator'], inplace=True)

# #all_grocery_stores = all_grocery_stores.append(grocery_stores_df)